In [1]:
import numpy as np
from numpy.fft import fft, ifft
import pandas as pd
import math
import plotly.express as px
import time
import random
import timeit
import re
import dill
from Genera_Q_omega import genera_q_omega

# Funciones auxiliares
<hr>

In [2]:
def genera_pol(grado):
    pol = []
    for i in range(grado):
        pol.append(random.randint(0,30))
        
    return pol

def genera_pols(grado):
    return [genera_pol(grado), genera_pol(grado)]

In [3]:
timeit.template = """
def inner(_it, _timer{init}):
    {setup}
    _t0 = _timer()
    for _i in _it:
        retval = {stmt}
    _t1 = _timer()
    return _t1 - _t0, retval
"""
## Modificamos la plantilla de timeit para que nos devuelva el resultaldo de la función

def measure_time(func, pols, mod=None, omega=None, PHI=None):
    if not mod and not omega:
        t = timeit.Timer(lambda: "-".join(map(str,func(pols))))
    else:
        t = timeit.Timer(lambda: "-".join(map(str,func(pols, mod, omega, PHI))))
        
    return t.timeit(number=100)
#     return timeit.timeit(lambda: "-".join(map(str,func(pols))), number=100)

# Usual implementation
<hr>

In [4]:
def multiplicacion_normal(pols):
    pol1 = pols[0]
    pol2 = pols[1]
    
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    num_terminos = longitud_pol1 + longitud_pol2 - 1
    res = [0]*num_terminos # Creamos la lista con tantos 0's como términos vaya a haber: 
    # El número de términos vendrá determinado por la suma de los grados + 1 (el término independiente)
    # (num_terminos_1 - 1) <- grado 1
    # (num_terminos_2 - 1) <- grado 2
    # grado_1 + grado_2 + 1 -> num_terminos_1 - 1 + num_terminos_2 - 1 + 1 = num_terminos_1 + num_terminos_2 - 1

    for o1,i1 in enumerate(pol1): # n * O(n) = O(n^2)
        for o2,i2 in enumerate(pol2): # n * O(1) = O(n)
            orden = o1 + o2
            multiplicacion = i1 * i2
            
            res[orden] += multiplicacion # O(1)
    return res

In [5]:
print(multiplicacion_normal([[2,11,1,1,2,2,2,4],[1,7,1,1]]))

[2, 25, 80, 21, 21, 18, 19, 22, 32, 6, 4]


# Karatsuba algorithm
<hr>
Codigo refactorizado de:<br>
<a href="https://github.com/mkannwischer/polymul/blob/master/Python/02karatsuba.py">https://github.com/mkannwischer/polymul/blob/master/Python/02karatsuba.py</a>

In [6]:
def karatsuba_algoritmo(pol1, pol2):
    
    longitud_pols = len(pol1)
    
    if longitud_pols == 1:
        elem_1 = pol1[0]
        elem_2 = pol2[0]
        res = elem_1 * elem_2
        return [res]

    nhalf = longitud_pols//2
    
    # Orden es O(n/2) cada uno, viene dado por:
    # https://stackoverflow.com/questions/13203601/big-o-of-list-slicing
    # https://github.com/python/cpython/blob/c353764fd564e401cf47a5d9efab18c72c60014e/Objects/listobject.c#L440
    a1 = pol1[:nhalf]
    a0 = pol1[nhalf:]
    b1 = pol2[:nhalf]
    b0 = pol2[nhalf:]

    # Y = x^{n//2}
    # a = a_0 + Y a_1
    # b = b_0 + Y b_1
    # a*b = (a_0 + Y a_1)*(b_0 + Y b_1)
    #     = Y^2 a_1 b_1 + Y (a_0 b_1 + a_1 b_0) + a_0 b_0
    #     = Y^2 a_1 b_1 + Y ((a_0 + a_1)(b_0 + b_1) - a_1 b_1 - a_0 b_0) + a_0 b_0

    contador = 0
    a0a1 = []
    b0b1 = []
    
    for i in range(nhalf):
        suma_a = a0[i]+a1[i]
        a0a1.append(suma_a)
        
        suma_b = b0[i]+b1[i]
        b0b1.append(suma_b)
        
    z0 = karatsuba_algoritmo(a0, b0)
    z2 = karatsuba_algoritmo(a1, b1)
    z1 = karatsuba_algoritmo(a0a1, b0b1)
    
    longitud_z0 = len(z0)
    
    for i in range(longitud_z0):
        valor_z1 = z1[i]
        z1[i] = valor_z1-z0[i]-z2[i]
    
#     num_zeros_necesarios = 2*longitud_pols-1 # No sé si esta operación la quiere en dos operaciones o no
    num_zeros_parcial = 2*longitud_pols
    num_zeros_necesarios = num_zeros_parcial - 1
    
    c = [0]*num_zeros_necesarios
    
    for i in range(longitud_z0):
#         c[i] += z2[i] # Igual aquí, no sé si así o aún más descompuesto:
        valor_z2_i = z2[i]
        c[i] += valor_z2_i
        
        c[i+nhalf] += z1[i]
        c[i+2*nhalf] += z0[i]
    
    return c    

def multiplicacion_karatsuba(pols): 
    pol1 = pols[0]    
    pol2 = pols[1]
    
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    if longitud_pol1 > longitud_pol2:
        num_zeros_necesarios = longitud_pol1-longitud_pol2
        arr_zeros = [0]*num_zeros_necesarios
        pol2 += arr_zeros
        
    else:
        num_zeros_necesarios = longitud_pol2-longitud_pol1
        arr_zeros = [0]*num_zeros_necesarios
        pol1 += arr_zeros
    
    return karatsuba_algoritmo(pol1, pol2)

In [7]:
multiplicacion_karatsuba([[2,11,1,1,2,2,2,4],[1,7,1,1]])

[2, 25, 80, 21, 21, 18, 19, 22, 32, 6, 4, 0, 0, 0, 0]

# FFT
<hr>

### FFT Recursive Video
<hr>
https://www.youtube.com/watch?v=h7apO7q16V0 

In [8]:
# Recursive function of FFT
def video_recursive_fft(P):
    # P = [p_0, p_1, ..., p_n-1] coeff representation  
    n = len(P)
    
    # if input contains just one element
    if n == 1:
        return P
 
    middle = n//2
     
    # Divide between odd and even coefficients
    Pe = P[0::2]
    Po  = P[1::2]

    # Recursive fft for even coefficients
    Ye = video_recursive_fft(Pe)
 
    # Recursive fft for odd coefficients
    Yo = video_recursive_fft(Po)
 
    # Create empty resulting polynomial
    Y = [0]*n
    
    for k in range(middle):        
        
        # Calculate omegas of the nth roots in the unitary circle
        multiplicacion_parcial = np.pi * (-2j)
        multiplicacion_parcial_2 = multiplicacion_parcial * k
        exponente = multiplicacion_parcial_2 / n
        
        w = np.exp(exponente)
        
        w_yodd_k = w * Yo[k]
        yeven_k = Ye[k]
        
        Y[k] = yeven_k + w_yodd_k
        Y[k + middle] = yeven_k - w_yodd_k
     
    return Y

def video_recursive_ifft(P):
    # P = [p_0, p_1, ..., p_n-1] coefficient representation
    n = len(P)
    
    # if input contains just one element
    if n == 1:
        return P
 
    middle = n//2
     
    # Divide between odd and even coefficients
    Pe = P[0::2]
    Po  = P[1::2]

    # Recursive ifft for even coefficients
    Ye = video_recursive_ifft(Pe)
 
    # Recursive ifft for odd coefficients
    Yo = video_recursive_ifft(Po)
 
    # Create empty resulting polynomial
    Y = [0]*n
    
    for k in range(middle):        
        
        # Calculate omegas of the nth roots in the unitary circle
        multiplicacion_parcial = np.pi * (2j)
        multiplicacion_parcial_2 = multiplicacion_parcial * k
        exponente = multiplicacion_parcial_2 / n
        
        w = np.exp(exponente)
        
        w_yodd_k = w * Yo[k]
        yeven_k = Ye[k]
        
        Y[k] = yeven_k + w_yodd_k
        Y[k + middle] = yeven_k - w_yodd_k
     
    return Y

# def polynomial_product_video(pol1, pol2):
def polynomial_product_video(pols):
    pol1 = pols[0].copy()
    pol2 = pols[1].copy()
    # Suponiendo que viene en el formato correcto de: [x,x,x,x, 0,0,0,0]
    # o
    # sin suponerlo: 
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    max_longitud = None
    if longitud_pol1 > longitud_pol2:
        max_longitud = 2*longitud_pol1
    else:
        max_longitud = 2*longitud_pol2
    
    pol1 += [0] * (max_longitud-longitud_pol1)
    pol2 += [0] * (max_longitud-longitud_pol2)
    
    # fft calculations
    fft1 = video_recursive_fft(pol1)
    fft2 = video_recursive_fft(pol2)
    
    # Element wise multiplication    
    product = []
    for i in range(max_longitud):
        product_a_b = fft1[i]*fft2[i]
        product.append(product_a_b)
    
    # Inverse FFT calculation, partial result
    result = video_recursive_ifft(product)
    
    # Complete result
    resultado = [i/len(product) for i in result]
    
    return resultado

In [9]:
multiplication = polynomial_product_video([[1,1,0,0], [1,1,1,1]])
print([np.round(i, 4) for i in multiplication])
print([int(np.round(i.real)) for i in multiplication])

[(1-0j), (2-0j), (2-0j), (2+0j), (1+0j), 0j, 0j, 0j]
[1, 2, 2, 2, 1, 0, 0, 0]


### FFT numpy implementation
<hr>
https://jeremykun.com/2022/11/16/polynomial-multiplication-using-the-fft/

In [10]:
def poly_mul(pols):
    
    """Multiply two polynomials.
 
    p1 and p2 are arrays of coefficients in degree-increasing order.
    """
    
    pol1 = pols[0].copy()
    pol2 = pols[1].copy()
    
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    max_longitud = None
    if longitud_pol1 > longitud_pol2:
        max_longitud = 2*longitud_pol1
    else:
        max_longitud = 2*longitud_pol2
    
    pol1 += [0] * (max_longitud-longitud_pol1)
    pol2 += [0] * (max_longitud-longitud_pol2)
    
    ff_p1 = fft(pol1)    
    ff_p2 = fft(pol2)
    
    # Element wise multiplication    
    product = []
    for i in range(max_longitud):
        product_a_b = ff_p1[i]*ff_p2[i]
        product.append(product_a_b)
    
    inverted = ifft(product)
    
    return inverted

In [11]:
multiplication = poly_mul([[1,1,0,0], [1,1,1,1]])
print([np.round(i, 4) for i in multiplication])
print([int(np.round(i.real)) for i in multiplication])

[(1+0j), (2+0j), (2+0j), (2+0j), (1+0j), 0j, 0j, 0j]
[1, 2, 2, 2, 1, 0, 0, 0]


# NTT
<hr>

### NTT polynomial multiplication recursive implementation
<hr>
<h3>Operations in this ring:</h3>

$$\mathbb{Z}_q\left[X\right]/\left\langle X^N-1\right\rangle$$

In [12]:
def ntt_recursive(pol, q, omegas):
    n = len(pol)
    
    if n == 1:
        return pol
    
    even_pol = pol[0::2]
    odd_pol = pol[1::2]
    half_omegas = omegas[::2]
    
    even = ntt_recursive(even_pol, q, half_omegas)
    odd = ntt_recursive(odd_pol, q, half_omegas)
    
    # Create empty resulting polynomial
    Y = [0]*n
    
    middle = n//2
    
    for k in range(middle):
        w_odd_k = omegas[k] * odd[k]
        
        w_even_k = even[k]
        
        Y[k] = (w_even_k + w_odd_k) % q
        
        offset = k + middle
        Y[offset] = (w_even_k - w_odd_k) % q
    
    return Y


def intt_recursive(pol, q, omegas_inv):
    n = len(pol)
    
    if n == 1:
        return pol
    
    even_pol = pol[0::2]
    odd_pol = pol[1::2]
    half_omegas = omegas_inv[::2]
    
    even = intt_recursive(even_pol, q, half_omegas)
    odd = intt_recursive(odd_pol, q, half_omegas)
    
    # Create empty resulting polynomial
    Y = [0]*n
    
    middle = n//2
    
    for k in range(middle):
        w_odd_k = omegas_inv[k] * odd[k]
        
        w_even_k = even[k]
        
        Y[k] = (w_even_k + w_odd_k) % q
        
        offset = k + middle
        Y[offset] = (w_even_k - w_odd_k) % q
    
    return Y

In [13]:
def mult_ntt(pols, q=17, omega=4, phi=None):
    pol1 = pols[0]
    pol2 = pols[1]
    
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    mayor_longitud = 0
    
    if longitud_pol1 > longitud_pol2:
        pol2 += [0]*(longitud_pol1-longitud_pol2)
        mayor_longitud = longitud_pol1
    else:
        pol1 += [0]*(longitud_pol2-longitud_pol1)
        mayor_longitud = longitud_pol2

    omegas = [1]
    omegas_inv = [1]
    
    omega_inv = pow(omega, -1, q)
    
    for i in range(1,mayor_longitud):
        omega_anterior = omegas[i-1]
        omega_anterior_inv = omegas_inv[i-1]
        omegas.append(omega_anterior*omega % q)
        omegas_inv.append(omega_anterior_inv*omega_inv % q)
    
    ntt_1 = ntt_recursive(pol1, q, omegas)
    ntt_2 = ntt_recursive(pol2, q, omegas)
    
    # calculate the pointwise multiplication of the NTTs
    mult_ntt = []
    for i in range(mayor_longitud):
        mult_ntt.append(ntt_1[i] * ntt_2[i] % q)
    
    intt_res = intt_recursive(mult_ntt, q, omegas_inv)
    
    # calculate N^-1 as the inverse of N in Z_n
    N_inv = pow(mayor_longitud, -1, q)
    
    resultado_intt = []
    for i in range(mayor_longitud):
        resultado_intt.append(intt_res[i] * N_inv % q)
    
    return resultado_intt

In [14]:
mult_ntt([[1,1,2,3],[1,2,3,4]]) # mod X^4-1 mod q

[0, 3, 2, 14]

In [15]:
mult_ntt([[3,2,1,1],[4,3,2,1]])

[2, 3, 0, 14]

### NTT polynomial multiplication recursive implementation (negacyclic convolution)
<hr>
<h3>Operations in this ring:</h3>

$$\mathbb{Z}_q\left[X\right]/\left\langle X^N+1\right\rangle$$

In [16]:
def mult_ntt_negacyclic(pols, mod=17, omega=4, PHI=2):
    pol1 = pols[0]
    pol2 = pols[1]
    
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    mayor_longitud = 0
    
    if longitud_pol1 > longitud_pol2:
        pol2 += [0]*(longitud_pol1-longitud_pol2)
        mayor_longitud = longitud_pol1
    else:
        pol1 += [0]*(longitud_pol2-longitud_pol1)
        mayor_longitud = longitud_pol2
    
    omegas = [1]
    omegas_inv = [1]
    
    omega_inv = pow(omega, -1, mod)
    
    for i in range(1,mayor_longitud):
        omega_anterior = omegas[i-1]
        omega_anterior_inv = omegas_inv[i-1]
        omegas.append(omega_anterior*omega % mod)
        omegas_inv.append(omega_anterior_inv*omega_inv % mod)
    
    ############################# NUEVO ##################################
#     PHI = calculate_phi(mod, omega)
    PHI_INV = pow(PHI, -1, mod)
    
    pol1_2 = []
    pol2_2 = []
    
    iaPotenciasPhi = [1]
    iaPotenciasPhiInv = [1]
    
    temp = 1
    temp_inv = 1
    
    for i in range(1,mayor_longitud):
        temp = (temp*PHI)%mod
        iaPotenciasPhi.append(temp)
        
        temp_inv = (temp_inv*PHI_INV)%mod
        iaPotenciasPhiInv.append(temp_inv)
        
    for i in range(mayor_longitud):
        pol1_2.append((pol1[i]*iaPotenciasPhi[i])%mod)
        
        pol2_2.append((pol2[i]*iaPotenciasPhi[i])%mod)
        
    ######################################################################
    
    ntt_1 = ntt_recursive(pol1_2, mod, omegas)
    ntt_2 = ntt_recursive(pol2_2, mod, omegas)
    
    # calculate the pointwise multiplication of the NTTs
    mult_ntt = []
    for i in range(mayor_longitud):
        mult_ntt.append(ntt_1[i] * ntt_2[i] % mod)
    
#     print(f"Mult_NTT:{mult_ntt}")
    
    intt_res = intt_recursive(mult_ntt, mod, omegas_inv)
    # calculate N^-1 as the inverse of N in Z_n
    N_inv = pow(mayor_longitud, -1, mod)
    
    resultado_intt = []
    for i in range(mayor_longitud):
        resultado_intt.append(intt_res[i] * N_inv % mod)
#     print(f"INTT_res:{resultado_intt}")
    
    ############################# NUEVO ##################################
    result_final = []
    for i in range(mayor_longitud):
        result_final.append((resultado_intt[i]*iaPotenciasPhiInv[i])%mod)
    ######################################################################
    
    
    return result_final

In [17]:
mult_ntt_negacyclic([[1,1,2,3],[1,2,3,4]], 17, 4)

[2, 3, 12, 14]

# Idea
<hr>

In [18]:
# Codigo de las funciones de abajo:
# https://cs.stackexchange.com/questions/10318/the-math-behind-converting-from-any-base-to-any-base-without-going-through-base

def fromDigits(digits, b):
    """Compute the number given by digits in base b."""
    n = int(0)
    for d in digits:
        n = 10 * n + d
    return n

def transform_number(int_arr, max_digitos):
    # El número de ceros viene dado por la cantidad de dígitos que queremos ser capaces de representar. 
    nuevo_arr = []
    for i in int_arr:
        for j in range(max_digitos-1):
            nuevo_arr.append(0)
        nuevo_arr.append(i)
        
    polynomial_representation = fromDigits(nuevo_arr,10)
    
    return polynomial_representation

def split_number(number, max_digitos):
    result = []
    while number > 0:
        number, remainder = divmod(number, 10**max_digitos)
        result.append(remainder)
    
    return result[::-1]


def multiplicacion_polinomios_idea_general(pols):
    pol1 = pols[0]
    pol2 = pols[1]
    
    # https://stackoverflow.com/questions/5454030/how-efficient-is-pythons-max-function
    max_num_1, max_num_2 = max(pol1), max(pol2)
    max_num = None
    
    if max_num_1 > max_num_2:
        max_num = max_num_1
    else: 
        max_num = max_num_2
        
    longitud_pol1 = len(pol1)
    longitud_pol2 = len(pol2)
    
    max_grado_mas_1 = None
    if longitud_pol1 > longitud_pol2:
        max_grado_mas_1 = longitud_pol1  #max_grado_mas 1 porque longitud nos da también el término libre
    else:
        max_grado_mas_1 = longitud_pol2
        
    log_max_grado = math.log10(max_grado_mas_1)
    
    log_max_num = math.log10(max_num)
    log_max_num = 2*log_max_num
    
    suma_logs = log_max_grado + log_max_num
    
    max_digitos = math.ceil(suma_logs) # x//1 + 1 -> O(1) + O(1)
    
    pol1_representacion = transform_number(pol1, max_digitos)
    pol2_representacion = transform_number(pol2, max_digitos)
    
    pol_multiplicacion = pol1_representacion * pol2_representacion
    
    digits = split_number(pol_multiplicacion, max_digitos)
    
    return digits

In [19]:
def multiplicacion_polinomios_idea(pols):
    pol1 = pols[0]
    pol2 = pols[1]
    
    max_digitos = 8 # Ver complejidad de esto
    
    pol1_representacion = transform_number(pol1, max_digitos)
    pol2_representacion = transform_number(pol2, max_digitos)
    
    pol_multiplicacion = pol1_representacion * pol2_representacion
    
    digits = split_number(pol_multiplicacion, max_digitos)
    
    return digits

In [20]:
multiplicacion_polinomios_idea([[1,1], [1,1,1,1]])

[1, 2, 2, 2, 1]

In [21]:
multiplicacion_polinomios_idea_general([[1,1], [1,1,1,1]])

[1, 2, 2, 2, 1]

# Comparación de tiempos
<hr>

In [22]:
# EN esta de abajo no está NTT
funcs = [multiplicacion_normal, multiplicacion_karatsuba, poly_mul, polynomial_product_video, multiplicacion_polinomios_idea]
funcs_nombres = ["Normal", "Karatsuba", "Numpy FFT", "FFT video", "Idea"]

funcs_ntt = [mult_ntt, mult_ntt_negacyclic]
funcs_ntt_nombres = ["NTT", "NTT negacyclic"]

tiempos_infinitos = {}
tiempos_finitos = {}

for i in funcs_nombres:
    tiempos_infinitos[i] = []
for i in funcs_ntt_nombres:
    tiempos_finitos[i] = []

for i in range(2,15):
    grado = 2**i
    pols = genera_pols(grado)
    
    for func, nombre_func in zip(funcs, funcs_nombres):
        measured_time = measure_time(func, pols)
        tiempos_infinitos[nombre_func].append({'tiempo': measured_time[0], "grado":grado, 'pols': pols, 'resultado': measured_time[1]})
        ultimo_tiempo = tiempos_infinitos[nombre_func][-1]
        print(f"{nombre_func}: 'tiempo': {ultimo_tiempo['tiempo']}, 'grado': {ultimo_tiempo['grado']}")
    
    
    mod, omega, phi = genera_q_omega(grado, 2, 106033)
    
    for func_ntt, nombre_func_ntt in zip(funcs_ntt, funcs_ntt_nombres):
        measured_time = measure_time(func_ntt, pols, mod, omega, phi)
        tiempos_finitos[nombre_func_ntt].append({'tiempo': measured_time[0], "grado":grado, 'pols': pols, 'resultado': measured_time[1], 'modulo': mod, 'omega':omega})
        ultimo_tiempo = tiempos_finitos[nombre_func_ntt][-1]
        print(f"{nombre_func_ntt}: 'tiempo': {ultimo_tiempo['tiempo']}, 'grado': {ultimo_tiempo['grado']}")

Normal: 'tiempo': 0.00037960000000003546, 'grado': 4
Karatsuba: 'tiempo': 0.0010759000000000185, 'grado': 4
Numpy FFT: 'tiempo': 0.003921500000000133, 'grado': 4
FFT video: 'tiempo': 0.011171399999999831, 'grado': 4
Idea: 'tiempo': 0.0011174999999998825, 'grado': 4
NTT: 'tiempo': 0.001335799999999665, 'grado': 4
NTT negacyclic: 'tiempo': 0.0015429000000000137, 'grado': 4
Normal: 'tiempo': 0.0011761999999997386, 'grado': 8
Karatsuba: 'tiempo': 0.004046699999999959, 'grado': 8
Numpy FFT: 'tiempo': 0.003098800000000068, 'grado': 8
FFT video: 'tiempo': 0.0184909000000002, 'grado': 8
Idea: 'tiempo': 0.0025607999999994746, 'grado': 8
NTT: 'tiempo': 0.002682499999999699, 'grado': 8
NTT negacyclic: 'tiempo': 0.004866999999999955, 'grado': 8
Normal: 'tiempo': 0.003606999999999694, 'grado': 16
Karatsuba: 'tiempo': 0.012173600000000562, 'grado': 16
Numpy FFT: 'tiempo': 0.005020799999999603, 'grado': 16
FFT video: 'tiempo': 0.04054599999999997, 'grado': 16
Idea: 'tiempo': 0.005923400000000356, 'gr

In [23]:
df_log = pd.DataFrame()
df = pd.DataFrame()

df_ntt = pd.DataFrame()
df_ntt_log = pd.DataFrame()

for k,v in tiempos_infinitos.items():
    grados = [i["grado"] for i in tiempos_infinitos[k]]
    tiempo_list = [i["tiempo"] for i in tiempos_infinitos[k]]
    
    df["Número de términos"] = grados
    df_log["Número de términos"] = grados
    
    df[k] = tiempo_list
    
    tiempo_list_log = [math.log(i) for i in tiempo_list]
    
    df_log[k] = tiempo_list_log
    
for k,v in tiempos_finitos.items():
    grados = [i["grado"] for i in tiempos_finitos[k]]
    tiempo_list = [i["tiempo"] for i in tiempos_finitos[k]]
    
    df_ntt["Número de términos"] = grados
    df_ntt_log["Número de términos"] = grados
    
    df_ntt[k] = tiempo_list
    
    tiempo_list_log = [math.log(i) for i in tiempo_list]
    
    df_ntt_log[k] = tiempo_list_log
    

print(df)
print(df_ntt)

    Número de términos       Normal   Karatsuba  Numpy FFT  FFT video  \
0                    4     0.000380    0.001076   0.003922   0.011171   
1                    8     0.001176    0.004047   0.003099   0.018491   
2                   16     0.003607    0.012174   0.005021   0.040546   
3                   32     0.011405    0.033037   0.011888   0.091871   
4                   64     0.047123    0.102664   0.020957   0.201279   
5                  128     0.177225    0.301740   0.038029   0.453457   
6                  256     0.693803    0.924800   0.072123   0.962914   
7                  512     2.929678    2.621655   0.134676   2.073520   
8                 1024    12.100293    8.221263   0.292876   4.606598   
9                 2048    48.076411   24.483873   0.545040   9.566608   
10                4096   193.203824   73.124394   1.124275  20.255492   
11                8192   767.274132  218.579874   2.297977  43.126532   
12               16384  3110.701979  654.594860   4

In [24]:
# Grafica que muestra el tiempo que tarda la ejecución 50 veces de un algoritmo para una multiplicación de polinomios de un grado determinado
fig = px.line(df, x='Número de términos', y=df.columns[1:], markers=True)

fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01
))

# Show plot 
fig.show()

In [25]:
# Grafica que muestra el tiempo en escala logarítmica (log_e ó ln) que tarda la ejecución 50 veces de un algoritmo para una multiplicación de polinomios de un grado determinado
fig = px.line(df_log, x='Número de términos', y=df.columns[1:], markers=True)

fig.update_layout(legend=dict(
    yanchor="bottom",
    y=0.01,
    xanchor="right",
    x=0.99
))

# Show plot 
fig.show()

In [26]:
# Grafica que muestra el tiempo que tarda la ejecución 50 veces de un algoritmo para una multiplicación de polinomios de un grado determinado
fig = px.line(df_ntt, x='Número de términos', y=df_ntt.columns[1:], markers=True)

fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01
))

# Show plot 
fig.show()

In [27]:
# Grafica que muestra el tiempo en escala logarítmica (log_e ó ln) que tarda la ejecución 50 veces de un algoritmo para una multiplicación de polinomios de un grado determinado
fig = px.line(df_ntt_log, x='Número de términos', y=df_ntt.columns[1:], markers=True)

fig.update_layout(legend=dict(
    yanchor="bottom",
    y=0.01,
    xanchor="right",
    x=0.99
))

# Show plot 
fig.show()

<hr>

# Comparando resultados para comprobar que todos dan lo mismo
Sin tener en cuenta NTT, ya que por definición darán otros resultados

In [28]:
def convert_to_integer_array(string):
    numbers = []
    
    if "(" in string:
        numbers = re.findall(r'\((.*?)\)', string)
    else:
        numbers = string.split('-')
    
    for i in range(len(numbers)):
        if 'j' in numbers[i]:
            complex_number = complex(numbers[i])
            rounded_number = round(complex_number.real) + round(complex_number.imag) * 1j
            
            if rounded_number.imag == 0:
                rounded_number = int(rounded_number.real)
            
            numbers[i] = rounded_number
        else:
            numbers[i] = round(float(numbers[i]))
    
    return np.trim_zeros(numbers)

# string1 = "468-652-824-668-1301-1449-1537-1335-1211-842-741-774-208-114-20"
# string2 = "(467.99999999999994+0j)-(652+0j)-(824+0j)-(668+0j)-(1301+0j)-(1449+0j)-(1537+0j)-(1335+0j)-(1211+0j)-(842+0j)-(741+0j)-(774+0j)-(208+0j)-(113.99999999999989+0j)-(19.999999999999886+0j)-0j"
# string3 = "(467.9999999999999+3.552713678800501e-15j)-(651.9999999999999+2.805493437129639e-14j)-(823.9999999999999+4.606281314449178e-14j)-(668+9.806640122612139e-14j)-(1301-8.594478035097917e-15j)-(1449+8.845106691090491e-14j)-(1537-6.027366785969378e-14j)-(1335-2.627857753189614e-14j)-(1211+3.552713678800501e-15j)-(842.0000000000001-2.878848448951162e-14j)-(741.0000000000001-3.9202315146720245e-14j)-(774-1.0799099214430766e-13j)-(208+1.489050677496915e-15j)-(114-8.207918967151914e-14j)-(20+5.341316986192225e-14j)-(-1.1368683772161603e-13+3.056484132891187e-14j)"

# print(convert_to_integer_array(string1))
# print(convert_to_integer_array(string2))
# print(convert_to_integer_array(string3))

# >> [468, 652, 824, 668, 1301, 1449, 1537, 1335, 1211, 842, 741, 774, 208, 114, 20]
# >> [468, 652, 824, 668, 1301, 1449, 1537, 1335, 1211, 842, 741, 774, 208, 114, 20]
# >> [468, 652, 824, 668, 1301, 1449, 1537, 1335, 1211, 842, 741, 774, 208, 114, 20]


def all_equal(lst):
    for arr in lst[1:]:
        if not np.array_equal(lst[0], arr, equal_nan=True):
            return False
    return True

for i in range(13):
    resultados = []
    
    for algoritmo in tiempos_infinitos.keys():
        resultado = convert_to_integer_array(tiempos_infinitos[algoritmo][i]["resultado"])
        resultados.append(resultado)
    
    print(f"Todos los resultados tras multiplicación de polinomios de grados {2**(2+i)} son iguales: {all_equal(resultados)}")
    
    resultados.clear()

Todos los resultados tras multiplicación de polinomios de grados 4 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 8 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 16 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 32 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 64 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 128 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 256 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 512 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 1024 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 2048 son iguales: True
Todos los resultados tras multiplicación de polinomios de grados 4096 son iguales: True
Todos los resultados tras multiplicación de pol

<hr>

# Escribir en ficheros para comprobar con script de MatLab (check_NTT_mult.m) que los resultados de las NTTs han sido correctos
<br>
Se podría hacer con SciPy pero la precisión sería vaga, mejor con MatLab

In [29]:
text_NTT = ""
text_NTT_negacyclic = ""

for i,j in zip(tiempos_finitos["NTT"], tiempos_finitos["NTT negacyclic"]):
    text_NTT += str(i["pols"]).replace(", ", " ").replace("] [", "]; [")
    text_NTT += "\n"+str(i["modulo"])
    text_NTT += "\n["+i["resultado"].replace("-"," ")+"]\n"
    
    text_NTT_negacyclic += str(j["pols"]).replace(", ", " ").replace("] [", "]; [")
    text_NTT_negacyclic += "\n"+str(i["modulo"])
    text_NTT_negacyclic += "\n["+j["resultado"].replace("-"," ")+"]\n"

# # Specify the file path
file_path = "NTT_mults.txt"
file_path_negacyclic = "NTT_mults_negacyclic.txt"

# Open the file in write mode and write the text
with open(file_path, 'w') as file:
    file.write(text_NTT)
    
# Open the file in write mode and write the text
with open(file_path_negacyclic, 'w') as file:
    file.write(text_NTT_negacyclic)

<h1>Script de MatLab</h1>

<br>

```matlab
disp("************************** NTT *************************")
disp("************ Multiplication Over Zq/<X^n-1> ************")
readLinesFromFile("NTT_mults.txt")
disp(" ")
disp("******************** NTT NEGACYCLIC ********************")
disp("************ Multiplication Over Zq/<X^n+1> ************")
readLinesFromFile("NTT_mults_negacyclic.txt")

%%
function [resultado_minus1, resultado_plus1] = perform_operations(input_matrix, modulo)
    % Invert the input arrays
    aa = fliplr(input_matrix(1, :));
    bb = fliplr(input_matrix(2, :));
    
    % Calculate the length of the input arrays
    N = max(length(aa), length(bb));
    
    % Generate the deconvolution coefficients for x^N - 1
    deconv_coeffs = [1, zeros(1, N - 1), -1];
    
    % Convolution
    cc = conv(aa, bb);
    
    % Deconvolution with x^N - 1
    [qq, rr] = deconv(cc, deconv_coeffs);
    resultado_minus1 = mod(rr, modulo);
    resultado_minus1 = fliplr(resultado_minus1);
    resultado_minus1 = resultado_minus1(:,1:N);

    % Generate the deconvolution coefficients for x^N + 1
    deconv_coeffs_plus1 = [1, zeros(1, N - 1), 1];
    
    % Deconvolution with x^N + 1
    [qq2, rr2] = deconv(cc, deconv_coeffs_plus1);
    resultado_plus1 = mod(rr2, modulo);
    resultado_plus1 = fliplr(resultado_plus1);
    resultado_plus1 = resultado_plus1(:,1:N);
end


%%
function readLinesFromFile(filename)
    LogicalStr = {'false', 'true'};
    
    fileID = fopen(filename, 'r');

    lineIndex = 1;

    line = fgetl(fileID);
    while ischar(line)
        
        if mod(lineIndex,3)==1
            input = str2num(line);
        elseif mod(lineIndex, 3)==2
            modulo = str2double(line);
        else
            output = str2num(line);

            [resultado_minus1, resultado_plus1] = perform_operations(input, modulo);

            resultado_igual = 0;
            if contains(filename, "negacyclic")
                resultado_igual = isequal(output, resultado_plus1);
            else
                resultado_igual = isequal(output, resultado_minus1);
            end

            fprintf("Los resultados tras multiplicación de polinomios de grados %i son iguales: %s\n", ...
                length(input(1,:)), LogicalStr{resultado_igual + 1})

        end
        lineIndex = lineIndex + 1;
        
        line = fgetl(fileID);
    end
    
    fclose(fileID);

end

```

<h1>Output of MatLab script</h1>
<img src="Comprobacion_resultados_NTT.png">

### Salvamos el estado del notebook por si acaso

In [30]:
dill.dump_session('notebook_env_tiempos_generales.db')

# dill.load_session('notebook_env.db')

## Comparación NTT vs FFT

In [ ]:
# import dill


# dill.load_session('notebook_env_tiempos_generales.db')

# Time measurements for "multiplicacion_polinomios_idea"
<hr>

In [32]:
previous_time = 0

tiempos_prueba_split_number = []
tiempos_prueba_transform_number = []
tiempos_prueba_mult_numbers = []
tiempos_prueba_overall = []

for i in range(2, 1 + 2**13):
    if i%1000 == 0:
        print(i)
    pol1 = genera_pol(i)
    pol2 = genera_pol(i)
    
    start_overall = time.perf_counter()
    
    ############################### TRANSFORM NUMBERS ###############################
    start1 = time.perf_counter()
    number1 = transform_number(pol1, 8)
    end1 = time.perf_counter()
    time_taken1 = end1 - start1
    tiempos_prueba_transform_number.append(time_taken1)
    
    number2 = transform_number(pol2, 8)
    #################################################################################
    
    
    ############################### MULTIPLY NUMBERS ###############################
    start = time.perf_counter()
    mult = number1 * number2
    end = time.perf_counter()
    time_taken = end-start
    tiempos_prueba_mult_numbers.append(time_taken)
    ################################################################################
    
    
    ################################# SPLIT NUMBER #################################
    start = time.perf_counter()
    res = split_number(mult, 8)
    end = time.perf_counter()
    time_taken = end-start
    tiempos_prueba_split_number.append(time_taken)
    ################################################################################
    
    end_overall = time.perf_counter()
    time_taken_overall = end_overall - start_overall
    tiempos_prueba_overall.append(time_taken_overall)
    
    print(f"{i}: Time taken now: {time_taken_overall} vs previous_time: {previous_time}. Difference: {abs(time_taken_overall-previous_time)}")
    
    previous_time = time_taken_overall

2: Time taken now: 1.3399998351815157e-05 vs previous_time: 0. Difference: 1.3399998351815157e-05
3: Time taken now: 1.5400000847876072e-05 vs previous_time: 1.3399998351815157e-05. Difference: 2.0000024960609153e-06
4: Time taken now: 1.5400000847876072e-05 vs previous_time: 1.5400000847876072e-05. Difference: 0.0
5: Time taken now: 1.7499998648418114e-05 vs previous_time: 1.5400000847876072e-05. Difference: 2.0999978005420417e-06
6: Time taken now: 2.4900000425986946e-05 vs previous_time: 1.7499998648418114e-05. Difference: 7.400001777568832e-06
7: Time taken now: 2.3099999452824704e-05 vs previous_time: 2.4900000425986946e-05. Difference: 1.8000009731622413e-06
8: Time taken now: 2.600000152597204e-05 vs previous_time: 2.3099999452824704e-05. Difference: 2.900002073147334e-06
9: Time taken now: 3.06999991153134e-05 vs previous_time: 2.600000152597204e-05. Difference: 4.699997589341365e-06
10: Time taken now: 3.769999966607429e-05 vs previous_time: 3.06999991153134e-05. Difference: 7

225: Time taken now: 0.03060910000021977 vs previous_time: 0.0018388999997114297. Difference: 0.02877020000050834
226: Time taken now: 0.0021512000002985587 vs previous_time: 0.03060910000021977. Difference: 0.02845789999992121
227: Time taken now: 0.0019252999991294928 vs previous_time: 0.0021512000002985587. Difference: 0.00022590000116906594
228: Time taken now: 0.0019405000002734596 vs previous_time: 0.0019252999991294928. Difference: 1.5200001143966801e-05
229: Time taken now: 0.0039341000010608695 vs previous_time: 0.0019405000002734596. Difference: 0.00199360000078741
230: Time taken now: 0.002150700000129291 vs previous_time: 0.0039341000010608695. Difference: 0.0017834000009315787
231: Time taken now: 0.0021333000004233327 vs previous_time: 0.002150700000129291. Difference: 1.739999970595818e-05
232: Time taken now: 0.002098900000419235 vs previous_time: 0.0021333000004233327. Difference: 3.440000000409782e-05
233: Time taken now: 0.0021045000012236414 vs previous_time: 0.0020

301: Time taken now: 0.0034940000005008187 vs previous_time: 0.0028822999993280973. Difference: 0.0006117000011727214
302: Time taken now: 0.002919099999417085 vs previous_time: 0.0034940000005008187. Difference: 0.0005749000010837335
303: Time taken now: 0.0029407999991235556 vs previous_time: 0.002919099999417085. Difference: 2.1699999706470408e-05
304: Time taken now: 0.002953999999590451 vs previous_time: 0.0029407999991235556. Difference: 1.320000046689529e-05
305: Time taken now: 0.0030172000006132293 vs previous_time: 0.002953999999590451. Difference: 6.320000102277845e-05
306: Time taken now: 0.002989799999340903 vs previous_time: 0.0030172000006132293. Difference: 2.7400001272326335e-05
307: Time taken now: 0.0030029999998077983 vs previous_time: 0.002989799999340903. Difference: 1.320000046689529e-05
308: Time taken now: 0.0030262000000220723 vs previous_time: 0.0030029999998077983. Difference: 2.320000021427404e-05
309: Time taken now: 0.0030452999999397434 vs previous_time:

373: Time taken now: 0.004797300000063842 vs previous_time: 0.004374600001028739. Difference: 0.00042269999903510325
374: Time taken now: 0.005103900000904105 vs previous_time: 0.004797300000063842. Difference: 0.0003066000008402625
375: Time taken now: 0.004568500000459608 vs previous_time: 0.005103900000904105. Difference: 0.000535400000444497
376: Time taken now: 0.004261599999153987 vs previous_time: 0.004568500000459608. Difference: 0.0003069000013056211
377: Time taken now: 0.004484200000661076 vs previous_time: 0.004261599999153987. Difference: 0.00022260000150708947
378: Time taken now: 0.0043554000003496185 vs previous_time: 0.004484200000661076. Difference: 0.00012880000031145755
379: Time taken now: 0.004316500000641099 vs previous_time: 0.0043554000003496185. Difference: 3.889999970851932e-05
380: Time taken now: 0.00448809999943478 vs previous_time: 0.004316500000641099. Difference: 0.00017159999879368115
381: Time taken now: 0.004356499999630614 vs previous_time: 0.004488

463: Time taken now: 0.006623399998716195 vs previous_time: 0.00621329999921727. Difference: 0.00041009999949892517
464: Time taken now: 0.006273200000578072 vs previous_time: 0.006623399998716195. Difference: 0.0003501999981381232
465: Time taken now: 0.006133000000772881 vs previous_time: 0.006273200000578072. Difference: 0.0001401999998051906
466: Time taken now: 0.006124199999248958 vs previous_time: 0.006133000000772881. Difference: 8.800001523923129e-06
467: Time taken now: 0.006955299999390263 vs previous_time: 0.006124199999248958. Difference: 0.0008311000001413049
468: Time taken now: 0.006302200001300662 vs previous_time: 0.006955299999390263. Difference: 0.0006530999980896013
469: Time taken now: 0.006712200000038138 vs previous_time: 0.006302200001300662. Difference: 0.00040999999873747583
470: Time taken now: 0.007383399999525864 vs previous_time: 0.006712200000038138. Difference: 0.000671199999487726
471: Time taken now: 0.00670689999969909 vs previous_time: 0.00738339999

...

7836: Time taken now: 1.275994499999797 vs previous_time: 1.2764319000016258. Difference: 0.0004374000018287916
7837: Time taken now: 1.2707731000009517 vs previous_time: 1.275994499999797. Difference: 0.0052213999988453
7838: Time taken now: 1.2705227000005834 vs previous_time: 1.2707731000009517. Difference: 0.00025040000036824495
7839: Time taken now: 1.283801699999458 vs previous_time: 1.2705227000005834. Difference: 0.013278999998874497
7840: Time taken now: 1.2741162000020267 vs previous_time: 1.283801699999458. Difference: 0.00968549999743118
7841: Time taken now: 1.2725798999999824 vs previous_time: 1.2741162000020267. Difference: 0.0015363000020442996
7842: Time taken now: 1.2755279000011797 vs previous_time: 1.2725798999999824. Difference: 0.002948000001197215
7843: Time taken now: 1.282505700000911 vs previous_time: 1.2755279000011797. Difference: 0.00697779999973136
7844: Time taken now: 1.273426499999914 vs previous_time: 1.282505700000911. Difference: 0.009079200000996934

7910: Time taken now: 1.2964957000003778 vs previous_time: 1.306152099998144. Difference: 0.00965639999776613
7911: Time taken now: 1.294895800001541 vs previous_time: 1.2964957000003778. Difference: 0.0015998999988369178
7912: Time taken now: 1.2961635999999999 vs previous_time: 1.294895800001541. Difference: 0.0012677999984589405
7913: Time taken now: 1.306539100001828 vs previous_time: 1.2961635999999999. Difference: 0.010375500001828186
7914: Time taken now: 1.2956875000018044 vs previous_time: 1.306539100001828. Difference: 0.010851600000023609
7915: Time taken now: 1.2982646000018576 vs previous_time: 1.2956875000018044. Difference: 0.0025771000000531785
7916: Time taken now: 1.3049337999982527 vs previous_time: 1.2982646000018576. Difference: 0.006669199996395037
7917: Time taken now: 1.2992397999987588 vs previous_time: 1.3049337999982527. Difference: 0.005693999999493826
7918: Time taken now: 1.2978445000007923 vs previous_time: 1.2992397999987588. Difference: 0.00139529999796

7984: Time taken now: 1.3185481000000436 vs previous_time: 1.3199866000031761. Difference: 0.0014385000031325035
7985: Time taken now: 1.3307218000009016 vs previous_time: 1.3185481000000436. Difference: 0.012173700000857934
7986: Time taken now: 1.324279699998442 vs previous_time: 1.3307218000009016. Difference: 0.006442100002459483
7987: Time taken now: 1.3265678999996453 vs previous_time: 1.324279699998442. Difference: 0.002288200001203222
7988: Time taken now: 1.3349980999992113 vs previous_time: 1.3265678999996453. Difference: 0.008430199999565957
7989: Time taken now: 1.3193861999970977 vs previous_time: 1.3349980999992113. Difference: 0.015611900002113543
7990: Time taken now: 1.3213735000026645 vs previous_time: 1.3193861999970977. Difference: 0.0019873000055667944
7991: Time taken now: 1.3208847000023525 vs previous_time: 1.3213735000026645. Difference: 0.0004888000003120396
7992: Time taken now: 1.3314604999977746 vs previous_time: 1.3208847000023525. Difference: 0.0105757999

8058: Time taken now: 1.3432969999994384 vs previous_time: 1.3448334999993676. Difference: 0.0015364999999292195
8059: Time taken now: 1.3606472000028589 vs previous_time: 1.3432969999994384. Difference: 0.01735020000342047
8060: Time taken now: 1.3504070999988471 vs previous_time: 1.3606472000028589. Difference: 0.010240100004011765
8061: Time taken now: 1.344786400000885 vs previous_time: 1.3504070999988471. Difference: 0.00562069999796222
8062: Time taken now: 1.3438967000001867 vs previous_time: 1.344786400000885. Difference: 0.0008897000006982125
8063: Time taken now: 1.356979299998784 vs previous_time: 1.3438967000001867. Difference: 0.013082599998597289
8064: Time taken now: 1.3464851000026101 vs previous_time: 1.356979299998784. Difference: 0.010494199996173847
8065: Time taken now: 1.3427769999980228 vs previous_time: 1.3464851000026101. Difference: 0.0037081000045873225
8066: Time taken now: 1.3551669000007678 vs previous_time: 1.3427769999980228. Difference: 0.01238990000274

8132: Time taken now: 1.3817133999982616 vs previous_time: 1.3659571999996842. Difference: 0.015756199998577358
8133: Time taken now: 1.369188699998631 vs previous_time: 1.3817133999982616. Difference: 0.012524699999630684
8134: Time taken now: 1.3690695999976015 vs previous_time: 1.369188699998631. Difference: 0.00011910000102943741
8135: Time taken now: 1.3683563999984472 vs previous_time: 1.3690695999976015. Difference: 0.0007131999991543125
8136: Time taken now: 1.3823840000004566 vs previous_time: 1.3683563999984472. Difference: 0.014027600002009422
8137: Time taken now: 1.3706879999990633 vs previous_time: 1.3823840000004566. Difference: 0.011696000001393259
8138: Time taken now: 1.368270199996914 vs previous_time: 1.3706879999990633. Difference: 0.0024178000021493062
8139: Time taken now: 1.3802452999989328 vs previous_time: 1.368270199996914. Difference: 0.011975100002018735
8140: Time taken now: 1.3691358999967633 vs previous_time: 1.3802452999989328. Difference: 0.01110940000

In [33]:
df_prueba = pd.DataFrame()
df_prueba["tiempos_split_number"] = tiempos_prueba_split_number
df_prueba["tiempos_trasnform_number"] = tiempos_prueba_transform_number
df_prueba["tiempos_mult_numbers"] = tiempos_prueba_mult_numbers
df_prueba["tiempos_overall"] = tiempos_prueba_overall

In [34]:
fig = px.line(df_prueba, y=["tiempos_split_number", "tiempos_trasnform_number", "tiempos_mult_numbers", "tiempos_overall"], markers=True)

fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01
))

# Show plot 
fig.show()

In [35]:
# https://stackoverflow.com/questions/31139591/measuring-big-o-of-multiplication-in-python#:~:text=Python%20uses%20the%20Karatsuba%20multiplication,O(n%5E2).
# https://discuss.python.org/t/faster-large-integer-multiplication/13300
tiempos_split_number_divided = []
tiempos_transform_number_divided = []
tiempos_mult_numbers_divided = []

for i in range(len(tiempos_prueba_split_number)):
    tiempo_split = tiempos_prueba_split_number[i]
    tiempos_transform = tiempos_prueba_transform_number[i]
    tiempos_mult = tiempos_prueba_mult_numbers[i]
    
    tiempos_split_number_divided.append(tiempo_split/(pow(tiempo_split,math.log2(3))))
    tiempos_transform_number_divided.append(tiempos_transform/(pow(tiempos_transform,math.log2(3))))
    tiempos_mult_numbers_divided.append(tiempos_mult/pow(tiempos_mult, math.log2(3)))

In [36]:
df_prueba_log = pd.DataFrame()
df_prueba_log["tiempos_split_number_log"] = tiempos_split_number_divided
df_prueba_log["tiempos_transform_number_log"] = tiempos_transform_number_divided
df_prueba_log["tiempos_mult_numbers_divided_log"] = tiempos_mult_numbers_divided

fig = px.line(df_prueba_log, y=["tiempos_split_number_log", "tiempos_transform_number_log", "tiempos_mult_numbers_divided_log"], markers=True)

# Show plot 
fig.show()

In [37]:
dill.dump_session('notebook_env_tiempos_especificos.db')